In [50]:
import pandas as pd
from sklearn.model_selection import train_test_split
from statsmodels.stats.outliers_influence import variance_inflation_factor
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
import sklearn
import statsmodels
import statsmodels.formula.api as sm
import matplotlib.pyplot as plt
import seaborn as sns
import copy
import requests
import pprint
from xgboost import XGBClassifier
from urllib import parse
from bs4 import BeautifulSoup

# 지수 형태의 실수를 소수점 3자리까지 표기
pd.options.display.float_format = "{:.3f}".format

# 공유 폴더 경로
dirShare = "G:/.shortcut-targets-by-id/188U2ypi3eUvuInaixMTTbbFctprRo9e4/GYM살라빔"


In [41]:
# 라이브러리 버전 확인
print("pandas 현재 버전 : " + pd.__version__)
print("scikit-learn 현재 버전 : " + sklearn.__version__)
print("statsmodels 현재 버전 : " + statsmodels.__version__)
print("xgboost 현재 버전 : " + xgboost.__version__)

pandas 현재 버전 : 2.0.3
scikit-learn 현재 버전 : 1.3.0
statsmodels 현재 버전 : 0.14.0
xgboost 현재 버전 : 1.7.6


# 데이터 불러오고 전처리

In [25]:
# train.csv 데이터 프레임으로 불러오기
df = pd.read_csv(dirShare+"/data/train.csv")

# df 정보 확인
df.info()

# df 상위 10개 불러오기
df.head(10)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 301 entries, 0 to 300
Data columns (total 58 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   inst_id             301 non-null    int64  
 1   OC                  301 non-null    object 
 2   sido                301 non-null    object 
 3   sgg                 301 non-null    int64  
 4   openDate            301 non-null    int64  
 5   bedCount            296 non-null    float64
 6   instkind            300 non-null    object 
 7   revenue1            293 non-null    float64
 8   salescost1          293 non-null    float64
 9   sga1                293 non-null    float64
 10  salary1             293 non-null    float64
 11  noi1                293 non-null    float64
 12  noe1                293 non-null    float64
 13  interest1           293 non-null    float64
 14  ctax1               293 non-null    float64
 15  profit1             293 non-null    float64
 16  liquidAs

inst_id    OC       sido  sgg  openDate  bedCount          instkind  \
0        1  open  choongnam   73  20071228   175.000  nursing_hospital   
1        3  open  gyeongnam   32  19970401   410.000  general_hospital   
2        4  open   gyeonggi   89  20161228   468.000  nursing_hospital   
3        7  open    incheon  141  20000814   353.000  general_hospital   
4        9  open  gyeongnam   32  20050901   196.000  general_hospital   
5       11  open  gyeongnam  155  20020501   243.000  general_hospital   
6       14  open   gyeonggi  169  19820702   213.000  general_hospital   
7       15  open      busan   66  19871102   250.000  general_hospital   
8       16  open    jeonnam   91  20060922   280.000  nursing_hospital   
9       17  open      seoul    4  20000124    55.000  general_hospital   

         revenue1      salescost1            sga1  ...           debt2  \
0  4217530010.000           0.000  3961134739.000  ...   758993742.000   
1             NaN             NaN             NaN  ...             NaN   
2  1004521989.000   515483669.000   447219722.000  ...           0.000   
3 72507342181.000           0.000 70677397660.000  ... 37755010512.000   
4 49043538016.000           0.000 47656051197.000  ... 51432592890.000   
5 33580536703.000  9222996930.000 23727912054.000  ...           0.000   
6 22552179836.000  4449958166.000 16573328452.000  ... 19642026834.000   
7 64359169160.000 20758010719.000 40882537264.000  ... 35984818131.000   
8 12748392940.000   328697683.000 11076189315.000  ...           0.000   
9 41406077905.000  6624671265.000 35120182720.000  ... 34906729636.000   

   liquidLiabilities2      shortLoan2  NCLiabilities2       longLoan2  \
0       222876855.000           0.000   536116887.000   390000000.000   
1                 NaN             NaN             NaN             NaN   
2               0.000           0.000           0.000           0.000   
3     17018596586.000  9219427379.000 20736413926.000 15100000000.000   
4     30072585842.000 17593752360.000 21360007048.000 14108027465.000   
5     21861133888.000 17087136895.000    20000000.000           0.000   
6     13292026834.000 12155602473.000  6350000000.000  6230000000.000   
7     11219645317.000           0.000 24765172814.000 16000000000.000   
8     13113246330.000 12664417803.000    41962676.000           0.000   
9     19675893406.000 16365396427.000 15230836230.000  3400000000.000   

        netAsset2       surplus2  employee1  employee2  ownerChange  
0  2619290493.000 1271224493.000     62.000     64.000         same  
1             NaN            NaN    801.000    813.000         same  
2           0.000          0.000    234.000      1.000         same  
3 12954271998.000 7740829037.000    663.000    663.000         same  
4     5561941.000 9025549604.000    206.000    197.000         same  
5           0.000 5879003604.000    397.000    390.000         same  
6 18888294786.000 9174282922.000    221.000    246.000         same  
7 14217864484.000 9177282701.000    489.000    489.000         same  
8           0.000          0.000    243.000    243.000         same  
9 20244525873.000 9554580715.000    370.000    382.000         same  

[10 rows x 58 columns]

In [26]:
# 데이터 개수 확인하기
print("데이터 개수 : ", df.shape[0])

데이터 개수 :  301


In [27]:
# 숫자 형식의 컬럼의 기술통계값을 출력
df.describe()

inst_id     sgg     openDate  bedCount         revenue1  \
count  301.000 301.000      301.000   296.000          293.000   
mean   219.056  81.040 20050125.801   145.709  12881747447.993   
std    121.235  50.970    88938.154   118.924  20435433475.616   
min      1.000   1.000 19780124.000     0.000            0.000   
25%    112.000  37.000 20011017.000    52.750   3252111902.000   
50%    230.000  75.000 20071126.000   136.500   5524218104.000   
75%    321.000 123.000 20111021.000   193.000  12748392940.000   
max    428.000 178.000 20170607.000   656.000 151000000000.000   

           salescost1             sga1         salary1           noi1  \
count         293.000          293.000         293.000        293.000   
mean   2014902794.594  10332439064.089  5654114566.904  269615124.573   
std    7460270656.568  14938862491.946  8083342530.256  802370115.514   
min             0.000            0.000           0.000          0.000   
25%             0.000   2758200772.000  1626052720.000    8217133.000   
50%     210410492.000   4684074465.000  2659892367.000   43637641.000   
75%     910527771.000  10778762060.000  6363400069.000  205033071.000   
max   98503322990.000 103000000000.000 64035593950.000 9144170639.000   

                noe1  ...  receivableL2           debt2  liquidLiabilities2  \
count        293.000  ...       293.000         293.000             293.000   
mean   511587022.570  ...    222670.000  8146026488.788      3860583593.406   
std   1060379255.452  ...   3811496.447 12557995349.365      6797242094.076   
min            0.000  ...         0.000           0.000               0.000   
25%     80133952.000  ...         0.000  1283220350.000       285574118.000   
50%    183196506.000  ...         0.000  3784552900.000      1454049945.000   
75%    420333030.000  ...         0.000  8465053127.000      4364713622.000   
max   8686379500.000  ...  65242310.000 85088583901.000     68468775764.000   

           shortLoan2  NCLiabilities2       longLoan2        netAsset2  \
count         293.000         293.000         293.000          293.000   
mean   1510050431.986  4471247363.877  2709978815.423   5273919018.089   
std    2953412250.368  7659580436.397  4564001070.999  10812593821.248   
min             0.000           0.000           0.000 -20147802018.000   
25%             0.000    25578782.000           0.000   1017572570.000   
50%      85425488.000  1969746813.000  1100000000.000   2894969804.000   
75%    1567966980.000  4905441439.000  3360000000.000   5370284792.000   
max   17593752360.000 51503883627.000 32561472110.000 125000000000.000   

             surplus2  employee1  employee2  
count         293.000    291.000    288.000  
mean    978627865.256    142.546    134.326  
std    4688797890.975    160.191    151.062  
min   -2781506722.000      0.000      0.000  
25%             0.000     53.500     53.750  
50%             0.000     80.000     79.000  
75%     101444685.000    181.500    170.000  
max   68527297093.000   1200.000   1200.000  

[8 rows x 54 columns]

In [28]:
# 컬럼별 null 값 확인하기
df.shape[0] - df.count()

inst_id                0
OC                     0
sido                   0
sgg                    0
openDate               0
bedCount               5
instkind               1
revenue1               8
salescost1             8
sga1                   8
salary1                8
noi1                   8
noe1                   8
interest1              8
ctax1                  8
profit1                8
liquidAsset1           8
quickAsset1            8
receivableS1           8
inventoryAsset1        8
nonCAsset1             8
tanAsset1              8
OnonCAsset1            8
receivableL1           8
debt1                  8
liquidLiabilities1     8
shortLoan1             8
NCLiabilities1         8
longLoan1              8
netAsset1              8
surplus1               8
revenue2               8
salescost2             8
sga2                   8
salary2                8
noi2                   8
noe2                   8
interest2              8
ctax2                  8
profit2                8


In [29]:
# 아직 운영 중인 병원을 1로 변환
df.replace({"open":1},inplace=True)
# 폐업한 병원을 0으로 변환
df.replace({" close":0}, inplace=True)
# unique() 메서드를 통해 "OC" 컬럼의 데이터를 확인
df["OC"].unique()

array([1, 0], dtype=int64)

In [30]:
# 병원 정보에 NULL이 존재하는 부분을 다른 값으로 대체할 수 없음
# 병원의 매출, 비용, 이익, 직원 수와 같은 값을 다른 병원의 평균이나 중앙값으로 대체하면 안 됨
df.dropna(axis=0, inplace=True)

In [31]:
# 데이터 값이 0으로만 돼 있는 컬럼 삭제
df.drop(columns=["receivableL1", "receivableL2"], axis=1, inplace=True)
# 시군구 코드 삭제
df.drop(columns="sgg", axis=1, inplace=True)
# 병원 id는 분석에 있어서 의미가 없는 데이터이므로 삭제
df.drop(columns="inst_id",inplace=True)
# 데이터 프레임에서 drop 됐는지 확인
df.columns

Index(['OC', 'sido', 'openDate', 'bedCount', 'instkind', 'revenue1',
       'salescost1', 'sga1', 'salary1', 'noi1', 'noe1', 'interest1', 'ctax1',
       'profit1', 'liquidAsset1', 'quickAsset1', 'receivableS1',
       'inventoryAsset1', 'nonCAsset1', 'tanAsset1', 'OnonCAsset1', 'debt1',
       'liquidLiabilities1', 'shortLoan1', 'NCLiabilities1', 'longLoan1',
       'netAsset1', 'surplus1', 'revenue2', 'salescost2', 'sga2', 'salary2',
       'noi2', 'noe2', 'interest2', 'ctax2', 'profit2', 'liquidAsset2',
       'quickAsset2', 'receivableS2', 'inventoryAsset2', 'nonCAsset2',
       'tanAsset2', 'OnonCAsset2', 'debt2', 'liquidLiabilities2', 'shortLoan2',
       'NCLiabilities2', 'longLoan2', 'netAsset2', 'surplus2', 'employee1',
       'employee2', 'ownerChange'],
      dtype='object')

In [32]:
df_drop_obj = copy.deepcopy(df)
df_dr_obj_cols = df_drop_obj.columns.to_list()
# df_dr_obj_cols

In [33]:
df_drop_obj2 = copy.deepcopy(df_drop_obj)

# 컬럼 데이터 타입이 'object'인 컬럼 삭제
for i in range(len(df_dr_obj_cols)) : 
    if df_drop_obj.iloc[:,i].dtype == "object" : 
        df_drop_obj2.drop(columns=df_dr_obj_cols[i], inplace=True)

df_drop_obj = df_drop_obj2
df_drop_obj.info()

<class 'pandas.core.frame.DataFrame'>
Index: 277 entries, 0 to 296
Data columns (total 51 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   OC                  277 non-null    int64  
 1   openDate            277 non-null    int64  
 2   bedCount            277 non-null    float64
 3   revenue1            277 non-null    float64
 4   salescost1          277 non-null    float64
 5   sga1                277 non-null    float64
 6   salary1             277 non-null    float64
 7   noi1                277 non-null    float64
 8   noe1                277 non-null    float64
 9   interest1           277 non-null    float64
 10  ctax1               277 non-null    float64
 11  profit1             277 non-null    float64
 12  liquidAsset1        277 non-null    float64
 13  quickAsset1         277 non-null    float64
 14  receivableS1        277 non-null    float64
 15  inventoryAsset1     277 non-null    float64
 16  nonCAsset1   

In [34]:
# 병원 개/폐업 정보의 다중 회귀 분석과 검정 통계량 확인
Models1 = sm.ols("OC ~ " + "+".join(df_drop_obj.columns[1:]), data=df_drop_obj)
result1 = Models1.fit()
print(result1.summary())

                            OLS Regression Results                            
Dep. Variable:                     OC   R-squared:                       0.277
Model:                            OLS   Adj. R-squared:                  0.117
Method:                 Least Squares   F-statistic:                     1.731
Date:                Tue, 11 Jul 2023   Prob (F-statistic):            0.00383
Time:                        21:57:33   Log-Likelihood:                 164.83
No. Observations:                 277   AIC:                            -227.7
Df Residuals:                     226   BIC:                            -42.84
Df Model:                          50                                         
Covariance Type:            nonrobust                                         
                         coef    std err          t      P>|t|      [0.025      0.975]
--------------------------------------------------------------------------------------
Intercept              4.2750      2

In [35]:
# 독립변수 X와 종속변수 y로 분리
X = df_drop_obj.iloc[:,1:]
y = df_drop_obj.iloc[:,0]

In [36]:
# 독립변수들간 다중 공선성 확인, vif 지수 10 이상이면 변수 제거 고려
vif = pd.DataFrame()
vif["VIF Factor"] = [variance_inflation_factor(X.values,i) for i in range(X.shape[1])]
vif["features"] = X.columns
vif = vif.sort_values("VIF Factor").reset_index(drop=True)
vif

VIF Factor            features
0        2.366            bedCount
1        3.737            openDate
2        6.340        receivableS2
3        6.494        receivableS1
4       12.035          shortLoan2
5       14.965          shortLoan1
6       20.043         OnonCAsset2
7       20.224         OnonCAsset1
8       22.919           interest1
9       24.217           interest2
10      29.897            surplus2
11      31.027           employee2
12      41.860           employee1
13      48.952           longLoan2
14      49.235     inventoryAsset2
15      54.158           longLoan1
16      73.027            surplus1
17      90.878     inventoryAsset1
18     444.396               ctax1
19     458.244               ctax2
20     875.933             salary2
21     890.690             salary1
22    1660.333           tanAsset1
23    2097.574           tanAsset2
24    2439.246                noi2
25    4291.453                noi1
26    5106.947         quickAsset2
27    7295.320                noe1
28    8160.759             profit1
29   10810.648             profit2
30   11148.307                noe2
31   24079.756         quickAsset1
32  119411.267        liquidAsset1
33  251612.232        liquidAsset2
34  371660.042          salescost1
35  408022.937           netAsset1
36  408155.510          salescost2
37  459567.970  liquidLiabilities1
38  554973.927               debt2
39  611602.006               debt1
40  679487.737      NCLiabilities1
41  736307.160          nonCAsset1
42  849957.884           netAsset2
43  910385.951  liquidLiabilities2
44 1168339.480      NCLiabilities2
45 1471435.214                sga1
46 1622510.398                sga2
47 1972381.814          nonCAsset2
48 2720979.309            revenue1
49 3183231.571            revenue2

In [37]:
# vif 지수가 10미만인 컬럼명
vif[vif["VIF Factor"]<10.0]["features"]

0        bedCount
1        openDate
2    receivableS2
3    receivableS1
Name: features, dtype: object

In [38]:
df_drop_vif = df_drop_obj[["OC","bedCount", "openDate", "receivableS2", "receivableS1"]]

In [39]:
Models2 = sm.ols("OC ~ " + "+".join(df_drop_vif.columns[1:]), data=df_drop_vif)
result2 = Models2.fit()
print(result2.summary())

                            OLS Regression Results                            
Dep. Variable:                     OC   R-squared:                       0.021
Model:                            OLS   Adj. R-squared:                  0.006
Method:                 Least Squares   F-statistic:                     1.436
Date:                Tue, 11 Jul 2023   Prob (F-statistic):              0.222
Time:                        21:57:33   Log-Likelihood:                 122.81
No. Observations:                 277   AIC:                            -235.6
Df Residuals:                     272   BIC:                            -217.5
Df Model:                           4                                         
Covariance Type:            nonrobust                                         
                   coef    std err          t      P>|t|      [0.025      0.975]
--------------------------------------------------------------------------------
Intercept        3.6487      2.205      1.655   

In [ ]:
"""
vif 지수가 10 이상이라고 무조건 제거하면 안 됨!
"""

# 모델학습

In [42]:
df["OC"].value_counts()

OC
1    270
0      7
Name: count, dtype: int64

In [44]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=626, stratify=y)
print(X_train.shape)
print(X_test.shape)
print(y_train.shape)
print(y_test.shape)

(221, 50)
(56, 50)
(221,)
(56,)


In [47]:
model_xgb = XGBClassifier()
xgb_model = model_xgb.fit(X_train, y_train)

y_pred = xgb_model.predict(X_test)
y_pred_prob = xgb_model.predict_proba(X_test)[:1]

In [48]:
print(y_pred)

[1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1
 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]


In [49]:
print(y_pred_prob)

[[6.439090e-04 9.993561e-01]]


In [51]:
accuracy_score(y_test, y_pred)

0.9821428571428571

In [52]:
f1__score(y_test, y_pred)

0.9909909909909909

In [58]:
X2 = df_drop_vif.iloc[:,1:]
y2 = df_drop_vif.iloc[:,0]

X_train2, X_test2, y_train2, y_test2= train_test_split(X2, y2, test_size=0.2, random_state=626, stratify=y2)
print(X_train2.shape)
print(X_test2.shape)
print(y_train2.shape)
print(y_test2.shape)

model_xgb2 = XGBClassifier()
xgb_model2 = model_xgb2.fit(X_train2, y_train2)

y_pred2 = xgb_model2.predict(X_test2)
y_pred_prob2 = xgb_model2.predict_proba(X_test2)[:1]

print("정확도 : ",accuracy_score(y_test2, y_pred2))
print("f1 socre : ",f1_score(y_test2, y_pred2))

(221, 4)
(56, 4)
(221,)
(56,)
정확도 :  0.9821428571428571
f1 socre :  0.9909909909909909


# 병원 정보 api 불러오기

In [ ]:
"""
https://apis.data.go.kr/B551182/hospInfoServicev2/getHospBasisList?serviceKey=repbMvjCXw96iTs6wjKM3Htm1H480VcdawruKmikMmOYZF8aVD%2FrJDkfGoyLeTuS5Y1KEOzUrwwPIu87UQ9LbQ%3D%3D&pageNo=1&numOfRows=10&sidoCd=110000&sgguCd=110019&emdongNm=%EC%8B%A0%EB%82%B4%EB%8F%99&yadmNm=%EC%84%9C%EC%9A%B8%EC%9D%98%EB%A3%8C%EC%9B%90&zipCd=2010&clCd=11&dgsbjtCd=01&xPos=127.09854004628151&yPos=37.6132113197367&radius=3000
"""

In [2]:
serviceKey = "repbMvjCXw96iTs6wjKM3Htm1H480VcdawruKmikMmOYZF8aVD/rJDkfGoyLeTuS5Y1KEOzUrwwPIu87UQ9LbQ=="
serviceKeyDecoded = parse.unquote(serviceKey, 'UTF-8')

url = "http://apis.data.go.kr/B551182/hospInfoServicev2/getHospBasisList"
returnType="xml"
Pindex = 1
Psize = 1000


queryParams = '?' + parse.urlencode({ parse.quote_plus("serviceKey") : serviceKeyDecoded,
                                parse.quote_plus("numOfRows") : '10000',
                                parse.quote_plus("pageNo") : '2'
                                    })

res = requests.get(url + queryParams)

In [3]:
soup = BeautifulSoup(res.text, 'lxml-xml')
items = soup.find_all("item")

In [4]:
pprint.pprint(items)

[<item><addr>제주특별자치도 제주시 중앙로 337, 2층 (이도이동)</addr><clCd>31</clCd><clCdNm>의원</clCdNm><cmdcGdrCnt>0</cmdcGdrCnt><cmdcIntnCnt>0</cmdcIntnCnt><cmdcResdntCnt>0</cmdcResdntCnt><cmdcSdrCnt>0</cmdcSdrCnt><detyGdrCnt>0</detyGdrCnt><detyIntnCnt>0</detyIntnCnt><detyResdntCnt>0</detyResdntCnt><detySdrCnt>0</detySdrCnt><drTotCnt>1</drTotCnt><estbDd>20171011</estbDd><mdeptGdrCnt>0</mdeptGdrCnt><mdeptIntnCnt>0</mdeptIntnCnt><mdeptResdntCnt>0</mdeptResdntCnt><mdeptSdrCnt>1</mdeptSdrCnt><pnursCnt>0</pnursCnt><postNo>63207</postNo><sgguCd>390200</sgguCd><sgguCdNm>제주시</sgguCdNm><sidoCd>390000</sidoCd><sidoCdNm>제주</sidoCdNm><telno>064-702-8820</telno><XPos>126.5372469</XPos><YPos>33.4914902</YPos><yadmNm>더좋은이비인후과의원</yadmNm><ykiho>JDQ4MTYyMiM4MSMkMiMkOCMkMDAkMzgxMzUxIzUxIyQxIyQxIyQ4MiQyNjEwMDIjODEjJDEjJDIjJDgz</ykiho></item>,
 <item><addr>경기도 수원시 영통구 광교호수공원로 277, 2F-004~011호 (원천동, 광교중흥에스클래스)</addr><clCd>31</clCd><clCdNm>의원</clCdNm><cmdcGdrCnt>0</cmdcGdrCnt><cmdcIntnCnt>0</cmdcIntnCnt><cmdcResdntCnt>0</cmdc

In [15]:
len(items)

10000

In [5]:
def parse():
    try:
        ADDR = item.find("addr").get_text()
        CLCD = item.find("clCd").get_text()
        CLCDNM = item.find("clCdNm").get_text()
        EMDONGNM = item.find("emdongNm").get_text()
        ESTBDB = item.find("estbDd").get_text()
        POSTNO = item.find("postNo").get_text()
        SGGUCD = item.find("sgguCd").get_text()
        SGGUCDNM = item.find("sgguCdNm").get_text()
        SIDOCD = item.find("sidoCd").get_text()
        SIDOCDNM = item.find("sidoCdNm").get_text()
        XPOS = item.find("XPos").get_text()
        YPOS = item.find("YPos").get_text()
        YADMNM = item.find("yadmNm").get_text()
        YKIHO = item.find("ykiho").get_text()
        return {
            "주소":ADDR,
            "종별코드":CLCD,
            "종별코드명":CLCDNM,
            "읍면동":EMDONGNM,
            "개설일자":ESTBDB,
            "Post No.":POSTNO,
            "시군구코드":SGGUCD,
            "시군구코드명":SGGUCDNM,
            "시도코드":SIDOCD,
            "시도코드명":SIDOCDNM,
            "x좌표":XPOS,
            'y좌표':YPOS,
            "요양기관명":YADMNM,
            "암호화요양기호":YKIHO
        }
    except AttributeError as e:
        return {
            "주소":None,
            "종별코드":None,
            "종별코드명":None,
            "읍면동":None,
            "개설일자":None,
            "Post No.":None,
            "시군구코드":None,
            "시군구코드명":None,
            "시도코드":None,
            "시도코드명":None,
            "x좌표":None,
            'y좌표':None,
            "요양기관명":None,
            "암호화요양기호":None
        }

In [16]:
row = list()

for item in items : 
    row.append(parse())

In [17]:
df_api = pd.DataFrame(row)
df_api.head()

주소  종별코드 종별코드명   읍면동      개설일자 Post No.  \
0                               None  None  None  None      None     None   
1                               None  None  None  None      None     None   
2  서울특별시 강동구 고덕로 254, 2층 (명일동, 이화빌딩)    31    의원   명일동  20131126    05269   
3                               None  None  None  None      None     None   
4                               None  None  None  None      None     None   

    시군구코드 시군구코드명    시도코드 시도코드명          x좌표         y좌표        요양기관명  \
0    None   None    None  None         None        None         None   
1    None   None    None  None         None        None         None   
2  110002    강동구  110000    서울  127.1537015  37.5546840  더줌마취통증의학과의원   
3    None   None    None  None         None        None         None   
4    None   None    None  None         None        None         None   

                                             암호화요양기호  
0                                               None  
1                                               None  
2  JDQ4MTg4MSM1MSMkMiMkNCMkMDAkNDgxMTkxIzExIyQyIy...  
3                                               None  
4                                               None

In [18]:
df_api.shape[0] - df_api.count()

주소          6964
종별코드        6964
종별코드명       6964
읍면동         6964
개설일자        6964
Post No.    6964
시군구코드       6964
시군구코드명      6964
시도코드        6964
시도코드명       6964
x좌표         6964
y좌표         6964
요양기관명       6964
암호화요양기호     6964
dtype: int64

In [9]:
df_api.dropna(axis=0, how="any", inplace=True)
df_api.shape

(3036, 14)

In [10]:
df_api.to_csv(dirShare+"/data/병원정보api_day2.csv",sep=',', encoding="utf-8")

In [11]:
df_day1  = pd.read_csv(dirShare+"/data/병원정보api.csv")
df_day1.info()
df_day1.head(10)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2609 entries, 0 to 2608
Data columns (total 15 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   Unnamed: 0  2609 non-null   int64  
 1   주소          2609 non-null   object 
 2   종별코드        2609 non-null   int64  
 3   종별코드명       2609 non-null   object 
 4   읍면동         2609 non-null   object 
 5   개설일자        2609 non-null   int64  
 6   Post No.    2609 non-null   int64  
 7   시군구코드       2609 non-null   int64  
 8   시군구코드명      2609 non-null   object 
 9   시도코드        2609 non-null   int64  
 10  시도코드명       2609 non-null   object 
 11  x좌표         2609 non-null   float64
 12  y좌표         2609 non-null   float64
 13  요양기관명       2609 non-null   object 
 14  암호화요양기호     2609 non-null   object 
dtypes: float64(2), int64(6), object(7)
memory usage: 305.9+ KB


Unnamed: 0                              주소  종별코드 종별코드명     읍면동      개설일자  \
0           0         인천광역시 부평구 동수로 56, (부평동)     1  상급종합     부평동  19810806   
1          12     부산광역시 서구 대신공원로 26, (동대신동3가)     1  상급종합  동대신동3가  19900303   
2          29        인천광역시 중구 인항로 27, (신흥동3가)     1  상급종합   신흥동3가  19960322   
3          46          인천광역시 서구 신석로 70, (석남동)    11  종합병원     석남동  19930708   
4          60      강원특별자치도 춘천시 백령로 156, (효자동)    11  종합병원     효자동  19820708   
5          63      강원특별자치도 속초시 영랑호반길 3, (영랑동)    11  종합병원     영랑동  19830701   
6          64  강원특별자치도 영월군 영월읍 중앙1로 59, (영월읍)    11  종합병원     영월읍  19830701   
7         133         대구광역시 남구 대명로 153, (대명동)    11  종합병원     대명동  20090102   
8         149       인천광역시 부평구 부평대로 175, (청천동)    11  종합병원     청천동  19830511   
9         161       광주광역시 동구 천변우로 415,  (불로동)    11  종합병원     불로동  19830415   

   Post No.   시군구코드 시군구코드명    시도코드 시도코드명     x좌표    y좌표            요양기관명  \
0     21431  220003  인천부평구  220000    인천 126.725 37.485     가톨릭대학교인천성모병원   
1     49201  210006   부산서구  210000    부산 129.018 35.120          동아대학교병원   
2     22332  220004   인천중구  220000    인천 126.634 37.459    인하대학교의과대학부속병원   
3     22789  220005   인천서구  220000    인천 126.670 37.510  (의)성세의료재단 뉴성민병원   
4     24289  320500    춘천시  320000    강원 127.745 37.875          강원대학교병원   
5     24821  320300    속초시  320000    강원 128.589 38.216     강원특별자치도속초의료원   
6     26234  320006    영월군  320000    강원 128.465 37.186     강원특별자치도영월의료원   
7     42474  230001   대구남구  230000    대구 128.574 35.840           드림종합병원   
8     21364  220003  인천부평구  220000    인천 126.720 37.507           부평세림병원   
9     61488  240001   광주동구  240000    광주 126.915 35.145          서남대학교병원   

                                             암호화요양기호  
0  JDQ4MTYyMiM1MSMkMSMkMCMkODkkMzgxMzUxIzExIyQxIy...  
1  JDQ4MTAxMiM1MSMkMSMkMCMkODkkMzgxMzUxIzExIyQyIy...  
2  JDQ4MTYyMiM1MSMkMSMkMCMkODkkMzgxMzUxIzExIyQxIy...  
3  JDQ4MTYyMiM1MSMkMSMkMCMkODkkMzgxMzUxIzExIyQxIy...  
4  JDQ4MTYyMiM1MSMkMSMkNCMkODkkMzgxMzUxIzExIyQxIy...  
5  JDQ4MTYyMiM1MSMkMSMkNCMkODkkMzgxMzUxIzExIyQxIy...  
6  JDQ4MTYyMiM1MSMkMSMkNCMkODkkMzgxMzUxIzExIyQxIy...  
7  JDQ4MTYyMiM4MSMkMSMkMCMkODkkMzgxMzUxIzExIyQxIy...  
8  JDQ4MTYyMiM1MSMkMSMkMCMkODkkMzgxMzUxIzExIyQxIy...  
9  JDQ4MTYyMiM3MSMkMSMkMCMkODkkMzgxMzUxIzExIyQyIy...

In [19]:
df_day2  = pd.read_csv(dirShare+"/data/병원정보api_day2.csv")
df_day2.info()
df_day2.head(10)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3036 entries, 0 to 3035
Data columns (total 15 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   Unnamed: 0  3036 non-null   int64  
 1   주소          3036 non-null   object 
 2   종별코드        3036 non-null   int64  
 3   종별코드명       3036 non-null   object 
 4   읍면동         3036 non-null   object 
 5   개설일자        3036 non-null   int64  
 6   Post No.    3036 non-null   int64  
 7   시군구코드       3036 non-null   int64  
 8   시군구코드명      3036 non-null   object 
 9   시도코드        3036 non-null   int64  
 10  시도코드명       3036 non-null   object 
 11  x좌표         3036 non-null   float64
 12  y좌표         3036 non-null   float64
 13  요양기관명       3036 non-null   object 
 14  암호화요양기호     3036 non-null   object 
dtypes: float64(2), int64(6), object(7)
memory usage: 355.9+ KB


Unnamed: 0                                             주소  종별코드 종별코드명  \
0           2              서울특별시 강동구 고덕로 254, 2층 (명일동, 이화빌딩)    31    의원   
1          11                   광주광역시 서구 상무자유로 134, 3층 (치평동)    31    의원   
2          13     경기도 성남시 분당구 백현로101번길 12, 302호 (수내동, 세인프라자)    31    의원   
3          22        충청북도 청주시 청원구 충청대로 168, 4층 (주성동, 골든타임타워)    31    의원   
4          23                    서울특별시 강북구 도봉로 365, 6층 (수유동)    31    의원   
5          43                  충청남도 당진시 당진중앙1로 111, 3층 (읍내동)    31    의원   
6          47                     대구광역시 남구 월배로 470, 3층 (대명동)    31    의원   
7          73          서울특별시 강남구 도곡로 409, 401호 (대치동, 타워엠프리스)    31    의원   
8          75            서울특별시 중구 명동3길 6, 개양빌딩 12층 1호 (명동1가)    31    의원   
9          83  경기도 성남시 분당구 성남대로 912, 201,202호 (야탑동, 분당BYC빌딩)    31    의원   

    읍면동      개설일자  Post No.   시군구코드 시군구코드명    시도코드 시도코드명     x좌표    y좌표  \
0   명일동  20131126      5269  110002    강동구  110000    서울 127.154 37.555   
1   치평동  20150417     61963  240003   광주서구  240000    광주 126.849 35.151   
2   수내동  20090810     13595  310403  성남분당구  310000    경기 127.112 37.377   
3   주성동  20140521     28318  330103  청주청원구  330000    충북 127.496 36.671   
4   수유동  20150803      1054  110024    강북구  110000    서울 127.027 37.640   
5   읍내동  20120106     31770  340900    당진시  340000    충남 126.630 36.895   
6   대명동  20141119     42498  230001   대구남구  230000    대구 128.556 35.835   
7   대치동  20060105      6207  110001    강남구  110000    서울 127.055 37.497   
8  명동1가  20170726      4534  110017     중구  110000    서울 126.984 37.564   
9   야탑동  20070503     13506  310403  성남분당구  310000    경기 127.129 37.411   

         요양기관명                                            암호화요양기호  
0  더줌마취통증의학과의원  JDQ4MTg4MSM1MSMkMiMkNCMkMDAkNDgxMTkxIzExIyQyIy...  
1     더코성형외과의원  JDQ4MTYyMiM3MSMkMiMkMCMkMDAkMzgxNzAyIzExIyQxIy...  
2        더퀸즈의원  JDU4MTI3MSM1MSMkMiMkMCMkMDAkMzgxMTkxIzMxIyQxIy...  
3    더탄탄정형외과의원  JDQ4MTYyMiM1MSMkMiMkOCMkMDAkMzgxOTYxIzQxIyQxIy...  
4     더탑성형외과의원  JDQ4MTg4MSM1MSMkMiMkMCMkMDAkNTgxOTYxIzMxIyQxIy...  
5      더편한내과의원  JDQ4MTYyMiM2MSMkMiMkMiMkMDAkNDgxMzUxIzIxIyQxIy...  
6      더편한내과의원  JDQ4MTYyMiM4MSMkMiMkMCMkMDAkNDgxOTYxIzIxIyQxIy...  
7   더푸른이비인후과의원  JDQ4MTg4MSM1MSMkMiMkNCMkMDAkMzgxMTkxIzIxIyQxIy...  
8      더프리티영의원  JDQ4MTg4MSM1MSMkMiMkNCMkMDAkNTgxMzUxIzExIyQxIy...  
9      더하기빼기의원  JDU4MTI3MSM1MSMkMiMkMCMkMDAkMzgxOTYxIzMxIyQxIy...

In [21]:
df_day1.sort_values(by='종별코드', axis=0, ascending=True)

Unnamed: 0                                                 주소  종별코드  \
0              0                            인천광역시 부평구 동수로 56, (부평동)     1   
1             12                        부산광역시 서구 대신공원로 26, (동대신동3가)     1   
2             29                           인천광역시 중구 인항로 27, (신흥동3가)     1   
21           372                      강원특별자치도 홍천군 홍천읍 산림공원1길 17, 17    11   
20           371                    서울특별시 양천구 목동로 225, 홍익병원본관 (신정동)    11   
...          ...                                                ...   ...   
1057        5905               충청남도 당진시 당진중앙2로 103-8, (읍내동, 진원스타6층)    31   
1058        5913          경상남도 김해시 능동로155번길 2, 303호 (부곡동, 장유월드피아상가)    31   
1059        5919                충청북도 청주시 상당구 산성로92번길 6, (금천동, 203호)    31   
1079        5966                       부산광역시 동래구 충렬대로 415, 3층 (안락동)    31   
2608        9990  부산광역시 영도구 상리로 25, 가동 205.206호 (동삼동, 동삼그린힐아파트 상...    31   

     종별코드명     읍면동      개설일자  Post No.   시군구코드 시군구코드명    시도코드 시도코드명     x좌표  \
0     상급종합     부평동  19810806     21431  220003  인천부평구  220000    인천 126.725   
1     상급종합  동대신동3가  19900303     49201  210006   부산서구  210000    부산 129.018   
2     상급종합   신흥동3가  19960322     22332  220004   인천중구  220000    인천 126.634   
21    종합병원     홍천읍  19891106     25131  320013    홍천군  320000    강원 127.895   
20    종합병원     신정동  19930820      7937  110020    양천구  110000    서울 126.864   
...    ...     ...       ...       ...     ...    ...     ...   ...     ...   
1057    의원     읍내동  20110131     31770  340900    당진시  340000    충남 126.631   
1058    의원     부곡동  20030923     50981  380100    김해시  380000    경남 128.808   
1059    의원     금천동  20140602     28744  330101  청주상당구  330000    충북 127.504   
1079    의원     안락동  20220215     47796  210003  부산동래구  210000    부산 129.104   
2608    의원     동삼동  20150424     49089  210007  부산영도구  210000    부산 129.068   

        y좌표          요양기관명                                            암호화요양기호  
0    37.485   가톨릭대학교인천성모병원  JDQ4MTYyMiM1MSMkMSMkMCMkODkkMzgxMzUxIzExIyQxIy...  
1    35.120        동아대학교병원  JDQ4MTAxMiM1MSMkMSMkMCMkODkkMzgxMzUxIzExIyQyIy...  
2    37.459  인하대학교의과대학부속병원  JDQ4MTYyMiM1MSMkMSMkMCMkODkkMzgxMzUxIzExIyQxIy...  
21   37.691         홍천아산병원  JDQ4MTYyMiM1MSMkMSMkNCMkODkkMzgxMzUxIzExIyQxIy...  
20   37.528           홍익병원  JDQ4MTg4MSM1MSMkMSMkMCMkODkkMzgxMzUxIzExIyQxIy...  
...     ...            ...                                                ...  
1057 36.894      굿모닝비뇨기과의원  JDQ4MTYyMiM2MSMkMiMkMiMkMDAkMzgxNzAyIzQxIyQxIy...  
1058 35.203      굿모닝비뇨기과의원  JDQ4MTYyMiM4MSMkMiMkNCMkMDAkMzgxNzAyIzIxIyQxIy...  
1059 36.631    굿모닝소아청소년과의원  JDQ4MTYyMiM1MSMkMiMkOCMkMDAkMzgxOTYxIzMxIyQxIy...  
1079 35.197     굿모닝이비인후과의원  JDQ4MTAxMiM1MSMkMiMkMCMkMDAkNDgxMzUxIzExIyQxIy...  
2608 35.085          더조은의원  JDQ4MTAxMiM1MSMkMiMkMCMkMDAkMzgxNzAyIzUxIyQxIy...  

[2609 rows x 15 columns]

In [22]:
df_day2.sort_values(by='종별코드', axis=0, ascending=True)

Unnamed: 0                                       주소  종별코드 종별코드명   읍면동  \
0              2        서울특별시 강동구 고덕로 254, 2층 (명일동, 이화빌딩)    31    의원   명일동   
2019        6772               강원특별자치도 속초시 중앙로 164, (중앙동)    31    의원   중앙동   
2020        6774                 충청북도 충주시 남산11길 17, (교현동)    31    의원   교현동   
2021        6775         충청북도 청주시 상당구 남일면 효촌송암1길 3, (남일면)    31    의원   남일면   
2022        6776              충청북도 단양군 매포읍 평동18길 6, (매포읍)    31    의원   매포읍   
...          ...                                      ...   ...   ...   ...   
1014        3572  부산광역시 해운대구 센텀남대로 50, A402호 (우동, 센텀임페리얼)    31    의원    우동   
1015        3574                대구광역시 남구 봉덕로 12, 2층 (봉덕동)    31    의원   봉덕동   
1016        3576              충청북도 청주시 흥덕구 강서로 122, (강서동)    31    의원   강서동   
1007        3547               경기도 안산시 상록구 샘골로 112, (본오동)    31    의원   본오동   
3035        9997       경기도 남양주시 퇴계원면 퇴계원로 16, 202호 (세란빌딩)    31    의원  퇴계원면   

          개설일자  Post No.   시군구코드  시군구코드명    시도코드 시도코드명     x좌표    y좌표  \
0     20131126      5269  110002     강동구  110000    서울 127.154 37.555   
2019  20011101     24824  320300     속초시  320000    강원 128.592 38.205   
2020  20010503     27396  330200     충주시  330000    충북 127.945 36.967   
2021  20060406     28187  330101   청주상당구  330000    충북 127.508 36.589   
2022  20040705     27005  330002     단양군  330000    충북 128.299 37.034   
...        ...       ...     ...     ...     ...   ...     ...    ...   
1014  20070808     48060  210009  부산해운대구  210000    부산 129.131 35.168   
1015  19930814     42445  230001    대구남구  230000    대구 128.592 35.845   
1016  20140904     28378  330102   청주흥덕구  330000    충북 127.430 36.625   
1007  20060309     15541  311102   안산상록구  310000    경기 126.863 37.294   
3035  19880627     12122  311500    남양주시  310000    경기 127.141 37.648   

            요양기관명                                            암호화요양기호  
0     더줌마취통증의학과의원  JDQ4MTg4MSM1MSMkMiMkNCMkMDAkNDgxMTkxIzExIyQyIy...  
2019         삼성의원  JDQ4MTYyMiM1MSMkMiMkNCMkMDAkMzgxOTYxIzIxIyQxIy...  
2020         삼성의원  JDQ4MTYyMiM1MSMkMiMkOCMkMDAkMzgxOTYxIzExIyQxIy...  
2021         삼성의원  JDQ4MTYyMiM1MSMkMiMkOCMkMDAkMzgxOTYxIzIxIyQyIy...  
2022         삼성의원  JDQ4MTYyMiM1MSMkMiMkOCMkMDAkMzgxOTYxIzIxIyQxIy...  
...           ...                                                ...  
1014     미플러스센텀의원  JDQ4MTAxMiM1MSMkMiMkMCMkMDAkMzgxMTkxIzIxIyQxIy...  
1015       미플러스의원  JDQ4MTYyMiM4MSMkMiMkMCMkMDAkMzgxOTYxIzUxIyQxIy...  
1016        미하이의원  JDQ4MTYyMiM1MSMkMiMkOCMkMDAkMzgxMTkxIzExIyQxIy...  
1007   미즈피아산부인과의원  JDU4MTI3MSM1MSMkMiMkMCMkMDAkNDgxMzUxIzUxIyQxIy...  
3035       세란연합의원  JDQ4MTYyMiM1MSMkMiMkMCMkMDAkMzgxMTkxIzExIyQxIy...  

[3036 rows x 15 columns]